<a id='top'></a>

<a id='top'></a>

In [1]:
from IPython.display import HTML

HTML('''<script>
code_show=true; 
function code_toggle() {
 if (code_show){
 $('div.input').hide();
 } else {
 $('div.input').show();
 }
 code_show = !code_show
} 
$( document ).ready(code_toggle);
</script>
It is intended that users change the runbook in anyway they want including the code (API calls) and input parameters into the code.
The raw code for this IPython notebook is by default hidden for easier reading.
To toggle on/off the raw code, click <a href="javascript:code_toggle()">here</a>.''')

<a id='toc'></a>

# Security Notebook
----
----

## Introduction

Security practioners have quite a few number of workflows that require manual work, such as: 

 * Ensuring cloud services are configured per best practices
 * Reviewing findings from various AWS services 
 * Investiage, probe around suspicious activity
 * Enable (or disable) various security services in an account
 
**The goal of this Runbook is to help a cloud security practionaer complete above workflows**.  The runbook goes through all security services and gets the findings and helps security practioner .  For each service, it helps a security practioner to do the following things : Ensure AWS security services are setup in a good way, Analyze findings,  Setup (enable, disable, teardown), Probe and investigate various services.

The following are the security services supported by this runbook : CloudTrail, GuardDuty, Inspector, Security Hub.

Accordingly, the notebook has three sections - Best Practice Checks, Analysis and Findings, and Services Enablement


## How to Use
 * **Use Case: Review Security Posture and Findings**: Hit "Kernel" -> "Restart and Runall" 
 * **Use Case: Investigation** : Hit the raw code button (the first cell), go to the section you want to dig deep into (such as service or user, change the parameters and Hit "Kernel" -> "Restart and Runall" 

 ---
 ---

 ## Table of Contents

* [Best Practice Checks](#bpchecks)
     * [AWS CloudTrail](#cloudtrail-checks) : Checks for Multi Region enablement
     * [Guard Duty](#guardduty-checks) : Checks whether Guard Duty is enabled in all regions 
     * [Inspector Checks](#inspector-checks): Checks whether Inspector (network reachability) is enabled in all regions
     * [Security Hub Checks](#securityhub-checks) : Checks whether Security hub is enabled in all regions
 ---
* [Analysis and Findings](#analysis)
    * [AWS CloudTrail](#cloudtrail-checks)
        * [API Call Summary](#cloudtrail-summary) 
        * [Cloudtrail Service and EventName Analysis](#cloudtrail-analysis)
        * [Cloudtrail User Agent Analysis](#cloudtrail-useragents)
          * [Console Logins](#console-logins) : Summary of console logins
          * [Root Activity](#root-activity) : Summary of root activity
          * [Generic Service Activity](#service-activity) : Deeper analysis of a particular service 
          * [Generic API action](#user-activity) : Deeper analysis of a particular action / EventName
          * [Generic User Activity](#user-activity) : Deeper analysis of a particular user
  	
    * [Inspector Findings Analysis](#inspector-findings)  : Findings from AWS Inspector
    * [GuardDuty Findings](#guardduty-findings) : Findings from AWS Guard Duty
    * [FIndings by AMI](#findings-by-ami) : Consolidates findings from Inspector and Guard Duty
   
   * [Security Hub](#securityhub-findings)
        * [Security Hub Findings Analysis](#sh-get-insights)
        * [Security Hub Insights](#sh-get-insights)
   * [Macie](#macie)
---
* [Services Enablement](#enable-services)
  * [AWS CloudTrail](#cloudtrail-enable) : Enables CloudTrail in all regions
  * [Guard Duty](#guardduty-enable) : Enables GuardDuty in all regions
  * [Inspector](#inspector-enable) : Enables Inspector in all regions
  * [Security Hub](#securityhub-enable) : Enables Security Hub in all regions
  
---
---
This security notebook can be run and results can be expored to HTML in Slack

# Admin Activity
(module installs and python imports that are required for the runbook)

## Imports (import modules)

This section includes python modules that need to be imported for the runbook

In [2]:
import sys
sys.path.append('/usr/local/lib/python3.6/site-packages')
import boto3
import datetime
import pandas as pd
import logging
import datetime
import json
import numpy as np
import time
import matplotlib.pyplot as pyplot
import matplotlib.pyplot as plt
import matplotlib.style as style
from cloudgovernor.helpers import spend_helpers
from cloudgovernor.helpers import lib_helpers
from cloudgovernor.helpers import aws_helpers
from cloudgovernor.helpers import cloudtrail_helpers
#from cloudgovernor.vuln import inspector_deploy

from importlib import reload
import pathlib
from geolite2 import geolite2
from IPython.display import Markdown as md
import os

from IPython.display import display, HTML

pd.set_option('display.max_colwidth', -1)
reader = geolite2.reader()

INFO:botocore.credentials:Found credentials in shared credentials file: ~/.aws/credentials


<a id='bpchecks'></a>

# Section 1. Best Practice Checks
This run book checks whether AWS security service are enabled and are configured per best practices.
The following ar ethe security services covered :
 1. AWS Cloudtrail
 1. AWS GuradDuty
 1. AWS Inspector (Network Reachability Scans)
 1. Security Hub

<a id='cloudtrail-checks'></a>
 
### Check whether CloudTrail is Enabled 
Every new AWS account has Cloudtrail enabled by default, the runbook checks that the trail has the following best practice configurations: 
 * Whether cloudtrail is enabled (this is done automatically now for every account created)
 * Whether the events are stored in a bucket
 * Whether the cloudtrail is enabled for all regions

In [3]:
print ("Running checks for account : ", boto3.client('sts').get_caller_identity()['Account'])
region_arr = aws_helpers.get_region_array()
df_arr = []
for region in region_arr:
    cclient=boto3.client('cloudtrail',region_name=region)
    cdf = pd.DataFrame(cclient.describe_trails()['trailList'])
    cdf = cdf [[ 'Name', 'S3BucketName', 'IsMultiRegionTrail']]
    df_arr.append(cdf)
ctedf = pd.concat(df_arr)
display(HTML(ctedf.drop_duplicates().to_html(index=False)))

if False in ctedf.IsMultiRegionTrail.tolist() :
    display (md(""" #### All Trails are Not Multi Regional:![](https://s3.amazonaws.com/cloudgovernorimages/redcross.png )
    """))
else : 
     display (md(""" #### All Trails are Multi Regional:![](https://s3.amazonaws.com/cloudgovernorimages/greencheck.png )
    """))

Running checks for account :  221470125883


 #### All Trails are Not Multi Regional:![](https://s3.amazonaws.com/cloudgovernorimages/redcross.png )
    

<a id='guardduty-checks'></a>
### Check whether GuardDuty is Enabled
Guard Duty checks for threat across various AWS log data, including CloudTrail (AWS user and API activity in your accounts), Amazon VPC Flow Logs (network traffic data), and DNS Logs (name query patterns).  Though a bit noisy, best practice is to have it enabled, and look at teh findings every week or so (findings are organized in a consumable way in the [GuardDuty Findings](#guardduty-findings) section below).

This run book checks for whether Guard Duty is enabled in all regions.

In [4]:
region_arr = aws_helpers.get_region_array()
df_arr = []
for region in region_arr:
    gdf = pd.DataFrame()
    
    try :
        gdclient = boto3.client('guardduty',region_name=region)
        if len (gdclient.list_detectors()['DetectorIds']) > 0 :
            gdf = pd.DataFrame(gdclient.list_detectors()['DetectorIds'], columns=['DetectorIds'])
            gdf['region']=region
        else :
            
            gdf['DetectorIds'] = "NA"
            gdf['region']=region
        
        df_arr.append(gdf)
    except :
        
        pass
  
gdconcatdf = pd.concat(df_arr)

enableregionlist = gdconcatdf.region.tolist()
disableregionlist = list (set(region_arr)-set(enableregionlist))
display (md(""" #### Guard Duty is enabled in regions: {enableregionlist} ![](https://s3.amazonaws.com/cloudgovernorimages/greencheck.png )
    """.format(enableregionlist=enableregionlist)))

display (md(""" #### Guard Duty is enabled in regions: {disableregionlist}![](https://s3.amazonaws.com/cloudgovernorimages/redcross.png )
    """.format(disableregionlist=disableregionlist)))

display (md(""" #### Guard Duty Detector IDs and Regions in which the Service is Enabled """))
display(HTML(gdconcatdf.to_html(index=False)))

 #### Guard Duty is enabled in regions: ['ap-south-1', 'eu-west-3', 'eu-west-2', 'eu-west-1', 'ap-northeast-2', 'ap-northeast-1', 'sa-east-1', 'ca-central-1', 'ap-southeast-1', 'ap-southeast-2', 'eu-central-1', 'us-east-1', 'us-east-2', 'us-west-1', 'us-west-2'] ![](https://s3.amazonaws.com/cloudgovernorimages/greencheck.png )
    

 #### Guard Duty is enabled in regions: ['eu-north-1']![](https://s3.amazonaws.com/cloudgovernorimages/redcross.png )
    

 #### Guard Duty Detector IDs and Regions in which the Service is Enabled 

<a id='inspector-checks'></a>

### Inspector (Network Reachability Rules) Enablement Checks
Check whether network reachability rules are enabled

In [5]:
ec2_client = boto3.client('ec2')
display (md(""" #### Evaluating for Network Reachability Rules in all regions """ )) 

check_inspector = False

if check_inspector :
    for region in pd.DataFrame (ec2_client.describe_regions()['Regions']).RegionName.tolist():
        try :

            ins_client = boto3.client('inspector', region_name=region)

            template_arns =  ins_client.list_assessment_templates()['assessmentTemplateArns']

            df_arr= []
            for template_arn in template_arns:

                tdf = pd.DataFrame (ins_client.describe_assessment_templates(assessmentTemplateArns=[template_arn])['assessmentTemplates'])
                df_arr.append(tdf)


            if len (df_arr) > 0 and not  pd.concat(df_arr).empty  :
                rule_arns = [ item for sublist in pd.concat(df_arr)['rulesPackageArns'].tolist() for item in sublist ]

            if len (rule_arns) > 0 :
                df_arr = []

                for rule_arn in rule_arns:
                    rdf = pd.DataFrame ( ins_client.describe_rules_packages(rulesPackageArns=[rule_arn])['rulesPackages'])
                    df_arr.append(rdf)

                if len (pd.concat(df_arr).index) > 0 :

                    if 'Network Reachability' in pd.concat(df_arr).name.tolist():
                        display (md(""" ##### The following network reachability rules exist in region : {region} ![](https://s3.amazonaws.com/cloudgovernorimages/greencheck.png)  """.format (region=region) )) 
                        ndf = pd.concat(df_arr)
                        ndf = ndf [ ndf.name.str.contains("Network")]
                        display(HTML(ndf[['name','arn']].to_html(index=False)))

        except Exception as e: print(e)

 #### Evaluating for Network Reachability Rules in all regions 

<a id='securityhub-checks'></a>

### Security Hub
AWS Security Hub collects and aggregates findings from the AWS security services and has pre configured compliance checks for security standards (currently for CIS bench marks).  For security hub, we check the number of standards enabled in security hub service for each region.

(go to [top](#top))

In [6]:
# Since security hub is in latest boto3, make sure its installed
#!pip uninstall -y 
#!pip install 'botocore==1.12.61'
#!pip uninstall -y boto3
#!pip install boto3 

client = boto3.client('securityhub')
region_arr = aws_helpers.get_region_array()
df_arr = []
for region in region_arr:
    secdf = pd.DataFrame ( { "region": region, "Number of standards enabled in Security Hub Service" : len (pd.DataFrame (client.get_enabled_standards()['StandardsSubscriptions']).shape) }, index=[0] )
    df_arr.append(secdf)
secdfarr = pd.concat(df_arr)
display(HTML(secdfarr.to_html(index=False)))


<a id='analysis'></a>


#  Section 2.  AWS Security Services Findings and Analysis
This run book gathers results and findings from all AWS security services and presents it in such a way that a security team can take a look at the results, assess the state of security and take remediative/corrective actions based on the findings.

This section gathers API write Call data for the past 64 hours (change it as your workflows require) is organized the following way -

 * API call summary (which services are involved with API calls, what actions have been conducted and by what users)
 * API call user agent summary (which user agents have been used for various actions on services)
 * Deep dive analysis into a service (for a given service, what actions by which users and at what time).  By default, the runbook takes the first service, and users of the runbook can change it to any serivce they want to investigate)
 * Deep dive analysis into an user (for a given user what actions did the user take and at what time). By default, the runbook takes the first user, and users of the runbook can change it to any serivce they want to investigate)
 * Deep dive analysis into various actions (by default, the run book brings up Console Logins, the users of the run book can change it to any action)
 

<a id='cloudtrail-summary'></a>
 
 
 (go to [top](#top))

In [7]:
reload(cloudtrail_helpers)
endtime = datetime.datetime.now()  # Create start and end time for CloudTrail lookup
interval = datetime.timedelta(hours=48) 
starttime = endtime - interval
reload(cloudtrail_helpers)
eventdf = cloudtrail_helpers.get_events_all_df(starttime, endtime)

eventdf['Resources'] = eventdf['Resources'].astype(str)

oeventdf = eventdf.copy()

eventdf = eventdf.drop_duplicates(["EventSource","EventName"])


cdf_eventnames = eventdf.groupby( ["EventSource"] )['EventName'].agg(','.join).reset_index(name='EventNames')
cdf_eventnames = cdf_eventnames [["EventSource",'EventNames' ]]


display (md(""" ## API Calls (CloudTrail) Event Summary
            * Number of Event Sources (services): {noservices}
            * Number of Event Names (actions): {noactions}
            """.format(noservices=len(eventdf.EventSource.unique().tolist()),noactions=len(eventdf.EventName.unique().tolist())  )
           ))
display (md("### API Calls : List of Services and Actions "))

cdf_eventnames.to_csv("/tmp/eventsources-actions.csv")
link = lib_helpers.take_uploadfilename_return_link("eventsources-actions.csv", "notebooks/eventsources-actions.csv")
display (md("##### Download the csv of the below table [here]({link})".format(link=link) ) )

display(HTML(cdf_eventnames.drop_duplicates().to_html(index=False, justify="left")))

eventdf = oeventdf.copy()
eventdf = eventdf.drop_duplicates(["EventSource","EventName"])
eventdf["Username"] = eventdf["Username"].astype(str)
cdf_users = eventdf.groupby( ["EventSource" , "EventName"] )['Username'].agg(','.join).reset_index(name='Users')
cdf_users = cdf_users [["EventSource","EventName",'Users' ]]

display (md("### List of Actions and Users"))

cdf_eventnames.to_csv("/tmp/eventactions-users.csv")
link = lib_helpers.take_uploadfilename_return_link("eventactions-users.csv", "notebooks/eventactions-users.csv")
display (md("##### Download the csv of the below table [here]({link})".format(link=link) ) )

display(HTML(cdf_users.drop_duplicates().to_html(index=False, justify="left")))

eventdf = oeventdf.copy()
eventdf = eventdf.drop_duplicates(["EventSource","EventName"])
eventdf["awsRegion"] = eventdf["awsRegion"].astype(str)
cdf_users = eventdf.groupby( ["EventSource", "EventName" ] )['awsRegion'].agg(','.join).reset_index(name='Regions')
cdf_users = cdf_users [["EventSource","EventName", 'Regions' ]]

#display (md("### Event Sources by Users"))
#display(HTML(cdf_users.drop_duplicates().to_html(index=False, justify="left")))




 ## API Calls (CloudTrail) Event Summary
            * Number of Event Sources (services): 16
            * Number of Event Names (actions): 51
            

### API Calls : List of Services and Actions 

##### Download the csv of the below table [here](https://console.aws.amazon.com/s3/object/cloudgovernor-221470125883/notebooks/eventsources-actions.csv)

### List of Actions and Users

##### Download the csv of the below table [here](https://console.aws.amazon.com/s3/object/cloudgovernor-221470125883/notebooks/eventactions-users.csv)

<a id='cloudtrail-useragents'></a>

###  User Actions and User Agents
User agents are finger prints of user actions.  This section gives a view of which user agents are being used for various action and corresponding services.

Events with cosole login user agents (non programmatic) user agents should be reviewed every day and followup to see why console logins are being used for actions.

(go to [top](#top))

In [8]:

eventdf = oeventdf.copy()

eventdf = eventdf.drop_duplicates(["EventName","userAgent"])
eventdf.userAgent = eventdf.userAgent.astype(str)
eventdf = eventdf.groupby( ["EventSource", "EventName","Username", 'sourceIPAddress'] )['userAgent'].agg(','.join).reset_index(name='UserAgents')
eventdf = eventdf.groupby( ["EventSource",'UserAgents',"Username", 'sourceIPAddress'] )['EventName'].agg(','.join).reset_index(name='Eventnames')
cdf_eventnames = eventdf [["EventSource", "Eventnames","Username", 'UserAgents' ,'sourceIPAddress' ]]
cdf_eventnames.style.set_table_styles([dict(selector="th",props=[('max-width', '25px')])])
pd.set_option('display.max_colwidth', 100)
cdf_eventnames.to_csv("/tmp/users-agents-ips.csv")
link = lib_helpers.take_uploadfilename_return_link("users-agents-ips.csv", "notebooks/users-agents-ips.csv")
display (md("##### Download the csv of the below table [here]({link})".format(link=link) ) )

display (md("### Events with non console login User Agents"))
display(HTML(cdf_eventnames[~cdf_eventnames.UserAgents.str.contains("console")].drop_duplicates().to_html(index=False, justify="left" , border = 1)))



##### Download the csv of the below table [here](https://console.aws.amazon.com/s3/object/cloudgovernor-221470125883/notebooks/users-agents-ips.csv)

### Events with non console login User Agents

<a id='console-logins'></a>


### Console Login Activity

In [9]:
reload(cloudtrail_helpers)
endtime = datetime.datetime.now()  # Create start and end time for CloudTrail lookup
interval = datetime.timedelta(hours=48)
starttime = endtime - interval

readonly = "false" # change it to false if you want write events as well

eventdf = cloudtrail_helpers.get_events_df("EventName", "PutConfigRule", starttime, endtime, readonly)

eventdf.EventTime = pd.to_datetime(eventdf.EventTime, format='%m-%d-%Y:%H').apply(lambda x:x.strftime('%m-%d-%Y'))
sdf = eventdf[["EventTime", 'Username',  'userAgent', 'sourceIPAddress']]
sdf = sdf.groupby( ["EventTime", "userAgent", 'sourceIPAddress'] )['Username'].agg(','.join).reset_index(name='Usernames')



sdf.to_csv("/tmp/consolelogins.csv")
link = lib_helpers.take_uploadfilename_return_link("consolelogins.csv", "consolelogins.csv")
display (md("##### Download the csv of the below table [here]({link})".format(link=link) ) )

#sdf['country'] = sdf['sourceIPAddress'].apply (lambda x: reader.get(x)['country']['names']['en'] )

display(HTML(sdf.drop_duplicates().to_html(index=False, justify="left")))

#eventdf['country'] = eventdf['sourceIPAddress'].apply (lambda x: reader.get(x)['country']['names']['en'] )


sdf = eventdf.groupby( [ "EventTime", "EventName", 'Username', 'userAgent'] )["EventName"].count().unstack()


#sdf.plot(kind='bar', figsize=(15,15),  legend=True, colormap="gist_rainbow", stacked=True).legend(bbox_to_anchor=(1,1))





##### Download the csv of the below table [here](https://console.aws.amazon.com/s3/object/cloudgovernor-221470125883/consolelogins.csv)

<a id='root-activity'></a>


### Root Activity
This section brings up the root activity (`userIdentitype.type = Root`)

In [10]:
report_slack = True
section = 'root-activity'
eventdf = oeventdf.copy()

eventdf.userIdentity= eventdf.userIdentity.astype(str)
eventdf = eventdf [eventdf.userIdentity.str.contains("Root")]
eventdf = eventdf [['EventSource', 'EventName', 'Username', 'EventTime', 'sourceIPAddress']]
eventdf = eventdf.groupby( ['EventTime', "EventSource","Username", 'sourceIPAddress'] )['EventName'].agg(','.join).reset_index(name='Eventnames')

sdf.to_csv("/tmp/rootactivity.csv")
link = lib_helpers.take_uploadfilename_return_link("rootactivity.csv", "rootactivity.csv")
display (md("##### Download the csv of the below table [here]({link})".format(link=link) ) )



display(HTML(eventdf.to_html(index=False, justify="left")))

if report_slack and not eventdf.empty :
    uploadfile = '/tmp/'+section+'.html'
    eventdf.to_html(uploadfile)
    print ("reporting into Slack ", uploadfile)
    os.popen( 'python3 /home/ec2-user/SageMaker/slacksender.py ' + uploadfile + " " + section+'.html' + " "  + section )
    

##### Download the csv of the below table [here](https://console.aws.amazon.com/s3/object/cloudgovernor-221470125883/rootactivity.csv)

reporting into Slack  /tmp/root-activity.html


## API Investigation
The API investigation section lets the user dig deep into a given
 * Service
 * Action
 * User
 
 The section has a default service, action and user and the user can edit each of the sections for desired input for analysis.

<a id='service-activity'></a>


### API Call Analysis of Specific Service

This section does deeper analysis of a given service.  By default, the run book analyzes `s3.amazonaws.com` service, please edit the `service` variable in the code for analysis on any other service.  

( To edit the code go to [top](#top) section and click the option to toggle the code )

In [11]:

service_investigation = True
if service_investigation :
    reload(cloudtrail_helpers)
    endtime = datetime.datetime.now()  # Create start and end time for CloudTrail lookup
    interval = datetime.timedelta(hours=48)
    starttime = endtime - interval
    service = 'iam.amazonaws.com'  # Edit the service below 
    readonly = "false" # change to false if you want to get write events as well
    #eventdf = oeventdf.copy()
    eventdf = cloudtrail_helpers.get_events_df("EventSource", "s3.amazonaws.com", starttime, endtime, readonly)
    display (md("#### API Calls have been made on the below services:"))
    print (eventdf.EventSource.unique().tolist())
    display (md("#### The following are the keys available for display (by default, we are displaying EventTime, Username, UserAgent and requestParameters:"))

    print (eventdf.columns.tolist())
    display (md("#### Service selected to analyze: {service}".format(service=service)))
    eventdf = cloudtrail_helpers.get_events_df("EventSource", service, starttime, endtime, readonly )
    eventdf = eventdf [eventdf.EventSource.str.contains(service)]
    eventdf.requestParameters = eventdf.requestParameters.astype(str)

    sdf = eventdf[["EventTime", 'EventName','Username',  'userAgent', 'requestParameters']]

    sdf.to_csv("/tmp/api-service.csv")
    link = lib_helpers.take_uploadfilename_return_link("api-service.csv", "api-service.csv")
    display (md("##### Download the csv of the below table [here]({link})".format(link=link) ) )



    display(HTML(sdf.drop_duplicates().to_html(index=False, justify="left")))


    sdf = eventdf.groupby( [ "EventTime", 'Username', 'userAgent'] )["EventName"].count().unstack()


    #sdf.plot(kind='bar', figsize=(15,15),  legend=True, colormap="gist_rainbow", stacked=True).legend(bbox_to_anchor=(1,1))



#### API Calls have been made on the below services:

['s3.amazonaws.com']


#### The following are the keys available for display (by default, we are displaying EventTime, Username, UserAgent and requestParameters:

['AccessKeyId', 'CloudTrailEvent', 'EventId', 'EventName', 'EventSource', 'EventTime', 'ReadOnly', 'Resources', 'Username', 'additionalEventData', 'awsRegion', 'errorCode', 'errorMessage', 'eventID', 'eventName', 'eventSource', 'eventTime', 'eventType', 'eventVersion', 'recipientAccountId', 'requestID', 'requestParameters', 'responseElements', 'sourceIPAddress', 'userAgent', 'userIdentity', 'vpcEndpointId']


#### Service selected to analyze: iam.amazonaws.com

##### Download the csv of the below table [here](https://console.aws.amazon.com/s3/object/cloudgovernor-221470125883/api-service.csv)

<a id='action-activity'></a>

## API Call Analysis of Specific Action

This section does deeper analysis of a given action (EventName).  By default, the run book analyzes the first eventname service, please edit the `EventName` variable in the code for analysis on any other service.  

( To edit the code go to [top](#top) section and click the option to toggle the code )

In [12]:
EventName = 'CreateTrail'  # change user to any user above.

event_investigation=True
if event_investigation :
    reload(cloudtrail_helpers)
    endtime = datetime.datetime.now()  # Create start and end time for CloudTrail lookup
    interval = datetime.timedelta(hours=48)
    starttime = endtime - interval
    readonly = "false"
    #eventdf = oeventdf.copy()
    eventdf = cloudtrail_helpers.get_events_df("EventName", "RunInstances", starttime, endtime, readonly)
    display (md("#### The following actions have happened API Calls have been made on the below services:"))
    print (eventdf.EventName.unique().tolist())

    eventdf = cloudtrail_helpers.get_events_df("EventName", "GetUser", starttime, endtime, readonly)
    display (md("#### Service selected to analyze: {EventName}".format(EventName=EventName)))
    eventdf = eventdf [eventdf.EventName.str.contains(EventName)]
    eventdf.requestParameters = eventdf.requestParameters.astype(str)

    sdf = eventdf[["EventTime", 'EventName','Username',  'userAgent', 'requestParameters', 'sourceIPAddress', 'awsRegion']]

    sdf.to_csv("/tmp/api-actions.csv")
    link = lib_helpers.take_uploadfilename_return_link("api-actions.csv", "api-actions.csv")
    display (md("##### Download the csv of the below table [here]({link})".format(link=link) ) )


    display(HTML(sdf.drop_duplicates().to_html(index=False, justify="left")))


    sdf = eventdf.groupby( [ "EventTime", 'Username', 'userAgent'] )["EventName"].count().unstack()


    #sdf.plot(kind='bar', figsize=(15,15),  legend=True, colormap="gist_rainbow", stacked=True).legend(bbox_to_anchor=(1,1))







#### The following actions have happened API Calls have been made on the below services:

[]


#### Service selected to analyze: CreateTrail

##### Download the csv of the below table [here](https://console.aws.amazon.com/s3/object/cloudgovernor-221470125883/api-actions.csv)

<a id='user-activity'></a>
## Analysis of Specific User Actions

This section does deeper analysis of a given user (Username).  By default, the run book analyzes the user `root`, please edit the `user` variable in the code for analysis on any other service.  

( To edit the code go to [top](#top) section and click the option to toggle the code )

In [29]:

user_investigation = True
if user_investigation :
    reload(cloudtrail_helpers)
    user = 'root'  # change user to any user above.
    endtime = datetime.datetime.now()  # Create start and end time for CloudTrail lookup
    interval = datetime.timedelta(hours=24)
    starttime = endtime - interval
    readonly = "true"
    #events = cloudtrail_helpers.get_events_df("EventName", "ConsoleLogin", starttime, endtime)
    #eventdf = pd.DataFrame(events)

    #eventdf = cloudtrail_helpers.get_events_all_df(starttime, endtime)

    eventdf = oeventdf.copy()
    display (md("#### The following are the users involved :"))
    print (eventdf.Username.unique().tolist())

    display (md("#### The following are the users available for display (by default, we are displaying EventTime, Username, UserAgent and requestParameters:"))

    print (eventdf.columns.tolist())
    eventdf = cloudtrail_helpers.get_events_df("Username", user, starttime, endtime, readonly)
    display (md("#### Service selected to analyze: {user}".format(user=user)))
    eventdf = eventdf [eventdf.Username.str.contains(user, na = False)]
    eventdf.requestParameters = eventdf.requestParameters.astype(str)
    eventdf = eventdf[~eventdf.requestParameters.str.contains("Threat")]
    sdf = eventdf[["EventTime", 'EventName','Username',  'userAgent', 'requestParameters']]
    display(HTML(sdf.drop_duplicates().to_html(index=False, justify="left")))


    sdf = eventdf.groupby( [ "EventTime", 'Username', 'userAgent'] )["EventName"].count().unstack()


    #sdf.plot(kind='bar', figsize=(15,15),  legend=True, colormap="gist_rainbow", stacked=True).legend(bbox_to_anchor=(1,1))






#### The following are the users involved :

['watcher-uxrouter', 'bdda6e2710a23c92ae0706de4d29a3cb', 'venkatdev', 'cg-221470125883', 'root', 'leadchimptweepy-tweepy', 'leadchimp-lc', 'stockrow', 'securityhub', 'watcher-telemetry', 'configLambdaExecution', 'AWSConfig-ConfigRuleValidation', 'SageMaker']


#### The following are the users available for display (by default, we are displaying EventTime, Username, UserAgent and requestParameters:

['AccessKeyId', 'CloudTrailEvent', 'EventId', 'EventName', 'EventSource', 'EventTime', 'ReadOnly', 'Resources', 'Username', 'additionalEventData', 'apiVersion', 'awsRegion', 'errorCode', 'errorMessage', 'eventID', 'eventName', 'eventSource', 'eventTime', 'eventType', 'eventVersion', 'managementEvent', 'readOnly', 'recipientAccountId', 'requestID', 'requestParameters', 'resources', 'responseElements', 'sourceIPAddress', 'userAgent', 'userIdentity', 'vpcEndpointId']


#### Service selected to analyze: root

<a id='inspector-findings'></a>
## AWS Inspector Findings 
The runbook tries to get the findings from Amazon Inspector network reachability scans, which analyzes for instances open to Internet.  Network reachability scans do not an agent to be installed.  If you have not enabled AWS inspector network scans, go to the services enablement section below to enable. 



In [14]:
get_inspector_findings = True

if get_inspector_findings : 
    idf = pd.DataFrame()
    df_arr = []
    for region in pd.DataFrame (ec2_client.describe_regions()['Regions']).RegionName.tolist():
        try :
            ins_client = boto3.client('inspector', region_name=region)
            run_arns = ins_client.list_assessment_runs()['assessmentRunArns']
            if len (run_arns) > 0 :
                for run_arn in run_arns :
                    ins_client.describe_assessment_runs(assessmentRunArns=[run_arn])
                    rundf = pd.DataFrame ( ins_client.describe_assessment_runs(assessmentRunArns=[run_arn])['assessmentRuns'])
                    finding_arns = ins_client.list_findings( assessmentRunArns=[run_arn ])['findingArns']

                    for each_finding in finding_arns :

                        rdf = pd.DataFrame ( ins_client.describe_findings(findingArns=[ each_finding ]) ['findings'] )

                        df_arr.append(rdf)
                        #asdf = pd.DataFrame (ins_client.describe_findings(findingArns=[ each_finding ])['findings'])
                        #display(HTML(asdf.drop_duplicates().to_html(index=False)))


        except Exception as e: print(e)
    if len(df_arr) > 0 :
                idf = pd.concat(df_arr)

    #display(HTML(idf.to_html(index=False)))


    df = idf.copy()
    if df.empty:
        print ("Inspector Findings Not Available Yet ... Please run in a few minutes ")
    else :
        print (df.columns)
        df.assetAttributes = df.assetAttributes.astype(str)
        df['ami_id'] = df.assetAttributes.str.split('amiId').str.get(1).str.split(",").str.get(0).str.split(":").str.get(1)

        df['inspector_port'] = df.description.str.split("port").str.get(1).str.split(',') #.str.get(0)

        df['inspector_network_ami_count'] = df.groupby('ami_id')['ami_id'].transform('count')

        df = df [['ami_id','description','inspector_network_ami_count']]
        display(HTML(df.drop_duplicates().to_html(index=False)))




An error occurred (500) when calling the ListAssessmentRuns operation (reached max retries: 4): Internal Server Error
Could not connect to the endpoint URL: "https://inspector.eu-west-3.amazonaws.com/"
Could not connect to the endpoint URL: "https://inspector.eu-west-2.amazonaws.com/"
Could not connect to the endpoint URL: "https://inspector.sa-east-1.amazonaws.com/"
Could not connect to the endpoint URL: "https://inspector.ca-central-1.amazonaws.com/"
Could not connect to the endpoint URL: "https://inspector.ap-southeast-1.amazonaws.com/"
Index(['arn', 'assetAttributes', 'assetType', 'attributes', 'confidence',
       'createdAt', 'description', 'id', 'indicatorOfCompromise',
       'numericSeverity', 'recommendation', 'schemaVersion', 'service',
       'serviceAttributes', 'severity', 'title', 'updatedAt',
       'userAttributes'],
      dtype='object')


<a id='guardduty-findings'></a>
## AWS GuardDuty Findings 
The run book gets all the findings from AWS guard duty and organizes them pivoting on the `ami_id` involved.

(go to [top](#top))


#### Get GuardDuty Findings
Guard Duty findings pivoted for each `ami_id` .  Inputs : Look back period, `num_days`

(go to [top](#top))

In [15]:
get_guardduty_findings = True

if get_guardduty_findings: 
    pd.set_option('display.max_colwidth', -1)
    num_days ='7'  # change the look back period

    regions = aws_helpers.get_region_array()
    df_arr = []

    for region in regions :
            try :
                client  = boto3.client('guardduty', region_name = region)
                DetectorIds = client.list_detectors()['DetectorIds']
                for did in DetectorIds :
                    fis = client.list_findings(DetectorId=did)['FindingIds']
                    for finding in fis:
                        finding_df = pd.DataFrame (client.get_findings(DetectorId=did, FindingIds= [finding] )['Findings'])
                        df_arr.append(finding_df)
            except :
                pass

    if len (df_arr) > 0 :
        gdf =  pd.concat(df_arr)
        gdf.Resource = gdf.Resource.astype(str)
        gdf.Service = gdf.Service.astype(str)
        gdf.region=gdf.Region
        gdf.UpdatedAt = pd.to_datetime(gdf.UpdatedAt)
        gdf = gdf[gdf.UpdatedAt > datetime.datetime.now() - pd.to_timedelta(num_days+"day")]

        tdf = gdf.copy()

        tdf.to_csv("/tmp/guardduty.csv")
        link = lib_helpers.take_uploadfilename_return_link("guardduty.csv", "notebooks/guardduty.csv")
        display (md("##### Download the csv of the below table [here]({link})".format(link=link) ) )

        tdf = tdf[tdf.Service.str.contains('AWS')]
        tdf = tdf [['Title', 'Service',  'Region', 'Severity','UpdatedAt']]

        display (md("### Guard Duty : AWS API Call Activity"))
        display(HTML(tdf.drop_duplicates().to_html(index=False)))

        display (md("### Guard Duty : EC2 Network Call Activity (PORT PROBEs not shown)"))
        tdf = gdf.copy()
        tdf = tdf[~tdf.Service.str.contains('AWS')]
        tdf = tdf[~tdf.Service.str.contains('PORT')]
        tdf['ami_id'] = tdf.Resource.str.split('ImageId').str.get(1).str.split(",").str.get(0).str.split(":").str.get(1)
        tdf.Service = tdf.Service.str.split('ActionType').str.get(1).str.split(",").str.get(0).str.split(":").str.get(1)
        tdf = tdf [['ami_id', 'Title', 'Service' ,  'Region', 'Severity']]
        print(tdf.columns)
        #print (tdf.groupby(['Resource','Region'])['Resource'].count())
        display(HTML(tdf.drop_duplicates().to_html(index=False)))
    else :
        print ("Guard Duty Findings Returned Empty")

/home/ec2-user/anaconda3/envs/python3/lib/python3.6/site-packages/ipykernel/__main__.py:26: UserWarning: Pandas doesn't allow columns to be created via a new attribute name - see https://pandas.pydata.org/pandas-docs/stable/indexing.html#attribute-access


##### Download the csv of the below table [here](https://console.aws.amazon.com/s3/object/cloudgovernor-221470125883/notebooks/guardduty.csv)

### Guard Duty : AWS API Call Activity

### Guard Duty : EC2 Network Call Activity (PORT PROBEs not shown)

Index(['ami_id', 'Title', 'Service', 'Region', 'Severity'], dtype='object')


<a id='findings-by-ami'></a>


### Which AMIs are more Risky ? Combining GuardDuty and Inspector Findings
This section combines findings from GuardDuty and Inspector 

In [16]:
#print (df.columns)
#print (tdf.columns)
try:
    if df.empty or tdf.empty :
        print ("")
except NameError:
    print ("guardduty or inspector findings not available")
else:
    cdf = pd.merge(df,tdf, left_on = 'ami_id', right_on='ami_id')
    #print (cdf.columns)
    display(HTML(cdf.drop_duplicates().to_html(index=False, justify="left")))



<a id='securityhub-findings'></a>
## AWS Security Hub Finding Analysis

### Get Findings from all regions

In [17]:
region_arr = aws_helpers.get_region_array()
df_arr = []
shdf = pd.DataFrame ()
try :
    for region in region_arr:
        client = boto3.client('securityhub',region_name = region)
        sdf = pd.DataFrame (client.get_findings()['Findings'])
        df_arr.append(sdf)


    shdf = pd.concat(df_arr)
    shdf['Resources'] = shdf['Resources'].dropna().astype(str)
    shdf['resource_arn'] = shdf['Resources'].str.split('\'Id\':').str.get(1).str.split(",").str.get(0)
    shdf['Resources'] = shdf['Resources'].dropna().astype(str)
    shdf['region'] = shdf.Resources.str.split('\'Region\':').str.get(1).str.split(",").str.get(0)

    shdf = shdf [['AwsAccountId', 'Title','Compliance', 'CreatedAt','Resources' ]]
    shdf = shdf [['AwsAccountId', 'Title','Compliance', 'CreatedAt','region', 'resource_arn']]
except Exception as e: print(e)

display(HTML(shdf.to_html(index=False, justify="left")))


Could not connect to the endpoint URL: "https://securityhub.eu-north-1.amazonaws.com/findings"


### Get Insights from all regions

In [18]:
region_arr = aws_helpers.get_region_array()
df_arr = []

try :
    for region in region_arr:
        client = boto3.client('securityhub',region_name = region)
        sdf = pd.DataFrame (client.get_insights()['Insights'])
        df_arr.append(sdf)

    shdf = pd.concat(df_arr)
    shdf = shdf [['AwsAccountId', 'Title','Compliance', 'CreatedAt','Resources']]
    display(HTML(shdf.to_html(index=False, justify="left")))
except Exception as e: print(e)




Could not connect to the endpoint URL: "https://securityhub.eu-north-1.amazonaws.com/insights/get"


<a id='enable-services'></a>


# Enable Disable Services

(go to [top](#top))

<a id='cloudtrail-enable'></a>

### CloudTrail

In [19]:
enable_ctrail = False # type True if you want to create a trail
account_id = boto3.client('sts').get_caller_identity()['Account']


trial_name = 'cgtrail'
trail_bucket = 'cg-'+account_id+'-trail'
cclient=boto3.client('cloudtrail')
if enable_ctrail :
    ccclient.create_trail(trail_name, s3_bucket_name=trail_bucket, IsMultiRegionTrail=True, include_global_service_events=True)

<a id='inspector-enable'></a>
## Inspector

(go to [top](#top))

<a id='inspector-enable'></a>
### Enable Network Vulns

In [20]:
enable_ins = False # True enables network reachability checks, False skips the code, will not enable network reachability checks
if enable_ins : 
    reload(inspector_deploy)
    ec2_client = boto3.client('ec2')
    for region in pd.DataFrame (ec2_client.describe_regions()['Regions']).RegionName.tolist():
        inspector_deploy.network_vuln_setup(region)

<a id='inspector-disable'></a>
### Disable Network Vulns
Note this will disable only the stuff that is enabled by this runbook.  Disabled , so not doing anything.

In [21]:
disable_ins = False

if disable_ins:
    ec2_client = boto3.client('ec2')
    for region in pd.DataFrame (ec2_client.describe_regions()['Regions']).RegionName.tolist():
        ins_client = boto3.client('inspector', region_name=region)

        try :

            if len (ins_client.list_assessment_targets(filter={ 'assessmentTargetNamePattern': 'cg-target-network' })['assessmentTargetArns']) > 0:
                try :
                    target_arn = ins_client.list_assessment_targets( filter={ 'assessmentTargetNamePattern': 'cg-target-network' } )['assessmentTargetArns'][0]                                                                                                                                     
                    response = ins_client.delete_assessment_target(assessmentTargetArn=target_arn)                                                                                                                                                                                                  
                    print (target_arn, response)                                                                                                                                                                                                                
                    # remove templates
                    template_arn = ins_client.list_assessment_templates(assessmentTargetArns=[ target_arn ] )['assessmentTemplateArns'][0]
                    response = ins_client.delete_assessment_template(assessmentTemplateArn=template_arn)
                    print (template_arn, response)

                    assessment_arn = ins_client.list_assessment_runs(assessmentTemplateArns=[template_arn ])['assessmentRunArns'][0]
                    response = ins_client.delete_assessment_run(assessmentRunArn=assessment_arn)
                    print ("assessment_arn", assessment_arn, response)
                except Exception as e: print(e)
        except Exception as e: print(e)

<a id='securityhub-enable'></a>

## Guard Duty

### Enable Guard Duty

In [22]:
#!pip uninstall -y 
#!pip install 'botocore==1.12.61'
#!pip uninstall -y boto3
#!pip install boto3 

import boto3
enable_gd = True
region_arr = aws_helpers.get_region_array()
df_arr = []
if enable_gd:
    for region in region_arr:
        try :
            gdclient = boto3.client('guardduty', region_name = region)
            print ("Enabled Guard Duty in ", region)
            response = gdclient.create_detector( Enable=True, FindingPublishingFrequency='ONE_HOUR')  #enable security hub
            
        except Exception as e: print(e)
            

Enabled Guard Duty in  eu-north-1
Could not connect to the endpoint URL: "https://guardduty.eu-north-1.amazonaws.com/detector"
Enabled Guard Duty in  ap-south-1
An error occurred (BadRequestException) when calling the CreateDetector operation: The request is rejected because a detector already exists for the current account.
Enabled Guard Duty in  eu-west-3
An error occurred (BadRequestException) when calling the CreateDetector operation: The request is rejected because a detector already exists for the current account.
Enabled Guard Duty in  eu-west-2
An error occurred (BadRequestException) when calling the CreateDetector operation: The request is rejected because a detector already exists for the current account.
Enabled Guard Duty in  eu-west-1
An error occurred (BadRequestException) when calling the CreateDetector operation: The request is rejected because a detector already exists for the current account.
Enabled Guard Duty in  ap-northeast-2
An error occurred (BadRequestException

<a id='securityhub-disable'></a>
### Disable Guard Duty

In [23]:
# aws events put-rule --name Test --event-pattern "{\"source\":[\"aws.guardduty\"],\"detail-type\":[\"GuardDuty Finding\"],\"detail\":{\"severity\":[7.0,7.1,7.2,7.3,7.4,7.5,7.6,7.7,7.8,7.9,8.0,8.1,8.2,8.3,8.4,8.5,8.6,8.7,8.8,8.9,7,8]}}"

In [24]:
disable_security_hub = False
disable_gd = False ## Change to True
region_arr = aws_helpers.get_region_array()
df_arr = []
if disable_security_hub :
    for region in region_arr:
        gdclient = boto3.client('guardduty', region_name = region)
        if disable_gd:
            try :
                DetectorId = gdclient.list_detectors()['DetectorIds'].tolist()[0]
                response = client.delete_detector(DetectorId=DetectorId)
                response = gdclient.create_detector( Enable=True, FindingPublishingFrequency='ONE_HOUR')  #enable security hub
            except Exception as e: print(e)

<a id='securityhub-enable'></a>

## Security Hub

### Enable Security Hub

In [25]:


enable_sh = False
client = boto3.client('securityhub')
region_arr = aws_helpers.get_region_array()
df_arr = []
if enable_sh:
    for region in region_arr:
        response = client.enable_security_hub() #enable security hub


<a id='securityhub-disable'></a>
### Disable Security Hub

In [26]:
# aws events put-rule --name Test --event-pattern "{\"source\":[\"aws.guardduty\"],\"detail-type\":[\"GuardDuty Finding\"],\"detail\":{\"severity\":[7.0,7.1,7.2,7.3,7.4,7.5,7.6,7.7,7.8,7.9,8.0,8.1,8.2,8.3,8.4,8.5,8.6,8.7,8.8,8.9,7,8]}}"

In [27]:
client = boto3.client('securityhub')
disable_security_hub = False ## Change to True
region_arr = aws_helpers.get_region_array()
df_arr = []
if disable_security_hub :
    for region in region_arr:
        if disable_security_hub:
            response = client.disable_security_hub()